In [1]:
import json
import pandas as pd
import geopandas as gpd
import folium
from shapely.geometry import Point, LineString

In [2]:
with open("location-history.json", "r", encoding="utf-8") as f:
    data = json.load(f)


In [3]:
print(type(data))
print("First element keys:", data[0].keys())


<class 'list'>
First element keys: dict_keys(['endTime', 'startTime', 'visit'])


In [4]:
print(len(data))
print(json.dumps(data[0], indent=2)[:1500])


5076
{
  "endTime": "2023-06-20T12:38:50.283+08:00",
  "startTime": "2023-06-20T00:23:01.081+08:00",
  "visit": {
    "hierarchyLevel": "0",
    "topCandidate": {
      "probability": "0.270366",
      "semanticType": "Unknown",
      "placeID": "ChIJ97fZE61hyzURQ6y3n2KLINc",
      "placeLocation": "geo:31.823620,117.210640"
    },
    "probability": "0.910000"
  }
}


In [14]:
visits = []
for item in data:
    if "visit" in item:
        v = item["visit"]
        top = v.get("topCandidate", {})
        place_str = top.get("placeLocation")
        if place_str and place_str.startswith("geo:"):
            try:
                lat, lon = map(float, place_str.replace("geo:", "").split(","))
                visits.append({
                    "lat": lat,
                    "lon": lon,
                    "placeId": top.get("placeID", ""),
                    "probability": top.get("probability", ""),
                    "start": item.get("startTime", ""),
                    "end": item.get("endTime", "")
                })
            except Exception as e:
                print("skip invalid coordinate:", place_str)

print(f"successully draw {len(visits)} points")


successully draw 1810 points


In [15]:
visits_df = pd.DataFrame(visits)
if len(visits_df) == 0:
    raise ValueError("no location data found")

gdf_visits = gpd.GeoDataFrame(
    visits_df,
    geometry=gpd.points_from_xy(visits_df.lon, visits_df.lat),
    crs="EPSG:4326"
)


In [26]:
import folium

# ---- 1️⃣ 固定地图视角与交互 ----
m = folium.Map(
    location=[30, 20],   # 全球中心点
    zoom_start=2.2,
    tiles="CartoDB positron",
    control_scale=False,
    zoom_control=False,
    dragging=False,
    scrollWheelZoom=False,
    doubleClickZoom=False,
    min_zoom=2,
    max_zoom=2
)

# ---- 2️⃣ 区分居住城市与访问城市 ----
for _, row in gdf_visits.iterrows():
    lat, lon = row.geometry.y, row.geometry.x

    # 判断是否为居住城市范围
    if (
        (39.8 < lat < 40.2 and -75.3 < lon < -74.8) or     # Philadelphia
        (51.3 < lat < 51.6 and -0.3 < lon < 0.1) or        # London
        (52.2 < lat < 52.5 and 4.7 < lon < 5.0) or         # Amsterdam
        (31.7 < lat < 31.9 and 117.1 < lon < 117.4)        # Hefei
    ):
        color = "red"
        cat = "Home City"
    else:
        color = "blue"
        cat = "Visited City"

    popup_text = f"<b>{cat}</b><br>Lat: {lat:.3f}, Lon: {lon:.3f}<br>{row['start']} → {row['end']}"
    folium.CircleMarker(
        location=[lat, lon],
        radius=4,
        color=color,
        fill=True,
        fill_opacity=0.8,
        popup=popup_text
    ).add_to(m)

# ---- 3️⃣ 城市标注：名字漂浮在海洋处 + 线连接 ----
# 坐标 (纬度, 经度)
city_labels = {
    "Philadelphia": {"city": [39.9526, -75.1652], "label": [38.5, -50]},   # 北大西洋
    "London":       {"city": [51.5074, -0.1278],  "label": [52.5, -30]},   # 北大西洋近西欧
    "Amsterdam":    {"city": [52.3676, 4.9041],   "label": [56.0, -25]},   # 英吉利海峡外海
    "Hefei":        {"city": [31.8206, 117.2272], "label": [33.0, 145.0]}  # 太平洋边
}

for name, loc in city_labels.items():
    city_lat, city_lon = loc["city"]
    label_lat, label_lon = loc["label"]

for name, loc in city_labels.items():
    city_lat, city_lon = loc["city"]
    label_lat, label_lon = loc["label"]

    # 计算线的比例终点（离文字留一点距离）
    shrink_factor = 0.9  # 越小线越短
    end_lat = city_lat + (label_lat - city_lat) * shrink_factor
    end_lon = city_lon + (label_lon - city_lon) * shrink_factor

    # 添加连接线（指向标注，虚线 & 不穿过文字）
    folium.PolyLine(
        locations=[[city_lat, city_lon], [end_lat, end_lon]],
        color="black",
        weight=1.2,
        opacity=0.8,
        dash_array="4,4"  # 4像素实线 + 4像素空白
    ).add_to(m)

    # 添加城市名文字
    folium.map.Marker(
        location=[label_lat, label_lon],
        icon=folium.DivIcon(
            html=f"""
            <div style="
                font-size:14px;
                color:black;
                font-weight:bold;
                text-shadow:1px 1px 2px white;
                white-space: nowrap;
                ">{name}</div>
            """
        )
    ).add_to(m)


# ---- 4️⃣ 显示地图 ----
m



In [9]:
# 或聚焦欧洲
m = folium.Map(location=[50, 10], zoom_start=4, tiles="CartoDB positron")

for _, row in gdf_visits.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=4,
        color="red",
        fill=True,
        fill_opacity=0.7
    ).add_to(m)


In [10]:
m